In [24]:
import numpy as np
import pandas as pd
import random

In [282]:
#### Miscellaneous functions
def sigmoid(z):
    """The sigmoid function."""
    return 1.0/(1.0+np.exp(-z))

def sigmoid_prime(z):
    """Derivative of the sigmoid function."""
    return sigmoid(z)*(1-sigmoid(z))

def one_hot(y):
    one_hot_y = np.zeros((y.size, 10))
    one_hot_y[np.arange(y.size), y] = 1
    one_hot_y = one_hot_y.T
    return one_hot_y

In [30]:
data = pd.read_csv("train.csv")
data = np.array(data)
m,n =  data.shape
np.random.shuffle(data)

data_dev = data[0:1000].T
Y_dev = data_dev[0]
X_dev = data_dev[1:n]

data_train = data[1000:m].T
Y_train = data_train[0]
X_train = data_train[1:n]

In [ ]:
def set_params(sizes):
    biases = [np.random.randn(x, 1) for x in sizes[1:]]
    weights = [np.random.randn(y, x) for x, y in zip(sizes[:-1], sizes[1:])]
    return weights, biases

def feed_forward(weights, biases, X):
    inputs = []
    activations = [X]
    for w, b, in zip(weights, biases):
        z = w.dot(activations[-1])
        a = sigmoid(z)
        activations.append(a)
        inputs.append(z)

    return inputs, activations

def back_propigation(inputs, activations, weights, X, Y):
    m = Y.size
    one_hot_Y = one_hot(Y)
    dW = []
    dB = []
    error = []
    error.append(activations[-1] - one_hot_Y)
    for i in range(1, 3):
        err = 1/m * 


In [243]:
def init_params():
    W1 = np.random.randn(10,784)
    b1 = np.random.randn(10, 1)
    W2 = np.random.randn(10,10)
    b2 = np.random.randn(10,1)
    return W1, b1, W2, b2

def forward_prop(W1, b1, W2, b2, X):
    Z1 = W1.dot(X) + b1
    A1 = sigmoid(Z1)
    Z2 = W2.dot(A1) + b2
    A2 = sigmoid(Z2)
    return Z1, A1, Z2, A2


def back_prop(Z1, A1, Z2, A2, W2, X, Y):
    m = Y.size
    one_hot_Y = one_hot(Y)
    dZ2 = A2 - one_hot_Y
    dW2 = 1/m * dZ2.dot(A1.T)
    db2 = 1/m * np.sum(dZ2, axis=1, keepdims=True)
    dZ1 = W2.T.dot(dZ2) * sigmoid_prime(Z1)

    dW1 = 1/m * dZ1.dot(X.T)
    db1 = 1/m * np.sum(dZ1, axis=1, keepdims=True)

    return dW1, db1, dW2, db2

def updata_params(W1, b1, W2, b2, dW1, db1, dW2, db2, alpha):
    W1 = W1 - alpha * dW1
    b1 = b1 - alpha * np.reshape(db1, (10,1))
    W2 = W2 - alpha * dW2
    b2 = b2 - alpha * np.reshape(db2, (10,1))
    return W1 ,b1, W2, b2

def get_predictions(A2):
    return np.argmax(A2, 0)

def get_accuracy(predictions, Y):
    print(predictions, Y)
    return np.sum(predictions == Y) / Y.size

def gradient_descent(X, Y, iterations, alpha):
    W1, b1, W2, b2 = init_params()
    for i in range(iterations):
        Z1, A1, Z2, A2 = forward_prop(W1, b1, W2, b2, X)
        dW1, db1, dW2, db2 = back_prop(Z1, A1, Z2, A2, W2, X, Y)
        W1, b1, W2, b2 = updata_params(W1, b1, W2, b2, dW1, db1, dW2, db2, alpha)
        if i % 50 == 0:
            print("iteration: ", i)
            print("Accuracy: ", get_accuracy(get_predictions(A2),Y))

    return W1, b1, W2, b2


In [244]:
W1, b1, W2, b2 = gradient_descent(X_train, Y_train, 200 , 3)

/var/folders/j4/g52zzpkn62b_d8zjk79rjddc0000gn/T/ipykernel_1937/4227189333.py:4: RuntimeWarning: overflow encountered in exp
  return 1.0/(1.0+np.exp(-z))


iteration:  0
[0 4 4 ... 0 4 0] [7 2 1 ... 0 9 5]
Accuracy:  0.10792682926829268
iteration:  50
[7 2 1 ... 0 7 3] [7 2 1 ... 0 9 5]
Accuracy:  0.5247560975609756
iteration:  100
[7 2 1 ... 0 6 3] [7 2 1 ... 0 9 5]
Accuracy:  0.6068048780487805
iteration:  150
[7 2 1 ... 0 6 3] [7 2 1 ... 0 9 5]
Accuracy:  0.6571951219512195


In [295]:
class Network:

    def __init__(self, sizes):
        self.size = sizes
        self.num_layers = len(sizes)
        self.biases = [np.random.randn(x, 1) for x in sizes[1:]]
        self.weights = [np.random.randn(y, x) for x, y in zip(sizes[:-1], sizes[1:])]
        
    def feed_forward(self, images):
        activations = [images]
        for w, b in zip(self.weights, self.biases):
            # print(w.shape, activations[-1].shape, b.shape)
            a = w.dot(activations[-1]) + b
            activations.append(sigmoid(a))
        return activations
    
    def evaluate(self, images, labels):
        activation = self.feed_forward(images)
        results = [(np.argmax(x), y) for x, y in zip(activation[-1].T, labels.T)]
        return sum(int(x == y) for (x, y) in results)
    
    def SGD(self, images, inlabels, epochs, LR, batch_size):
        targets = one_hot(inlabels)
        n = len(images.T)
        train_batches = [
                images[:,k:k+batch_size]
                for k in range(0, n, batch_size)]
        labels_batches = [
                targets[:,k:k+batch_size]
                for k in range(0, n, batch_size)]
        
        for j in range(0, epochs):
            for batch, labels in zip(train_batches, labels_batches):
                activations = self.feed_forward(batch)
                dw, db = self.back_prop(activations, labels)
                self.weights = [w-(LR/batch_size)*nw for w, nw in zip(self.weights, dw)]
                self.biases = [b-(LR/batch_size)*nb for b, nb in zip(self.biases, db)]
            self.evaluate(images, inlabels)
            
        return 0
    
    def back_prop(self, activations, targets):
        dw = [np.zeros(w.shape) for w in self.weights]
        db = [np.zeros(b.shape) for b in self.biases]
        errorOutput = targets - activations[-1]
        errors = [errorOutput]

        for l in range(1, self.num_layers):
            db[-l] = np.sum(errors[-1], axis=1, keepdims=True)
            print(db[-l])
            dw[-l] = np.dot(errors[-1], activations[-l-1].transpose())

            if l < self.num_layers -1:
                prev_err = np.dot(self.weights[-l].transpose(), errors[-1]) * sigmoid_prime(activations[-l-1])
                errors.append(prev_err)

        return dw, db

In [296]:
network = Network([784,30,10])
network.SGD(X_train, Y_train, 1, 3, 10)

/var/folders/j4/g52zzpkn62b_d8zjk79rjddc0000gn/T/ipykernel_1937/4227189333.py:4: RuntimeWarning: overflow encountered in exp
  return 1.0/(1.0+np.exp(-z))


[[-8.67431961]
 [-6.12456985]
 [-2.25364949]
 [-2.02977787]
 [-2.13316371]
 [-3.6250358 ]
 [-5.03974916]
 [-7.96368092]
 [-9.68385988]
 [-0.37343818]]
[[ -3.88468132]
 [  0.30992545]
 [  5.4892161 ]
 [ -1.69766257]
 [  1.64529047]
 [  5.7474818 ]
 [ -4.08916145]
 [ -4.64038135]
 [ -3.03805837]
 [  4.3410986 ]
 [ -2.11253714]
 [ -4.92912439]
 [ -3.64354852]
 [ -6.11423647]
 [-12.2114208 ]
 [  2.75321531]
 [ -7.5431821 ]
 [  3.35568089]
 [ -3.62310639]
 [ -3.1444265 ]
 [ -4.48395261]
 [ -5.99575952]
 [  6.717159  ]
 [ -1.78404009]
 [  5.22350676]
 [ -4.07756083]
 [  3.88389301]
 [ -8.50325162]
 [  3.28648307]
 [ -0.86521923]]
[[-10.        ]
 [ -9.        ]
 [ -5.28601186]
 [ -8.67549002]
 [ -8.99895649]
 [ -9.99999684]
 [ -8.99999995]
 [-10.        ]
 [ -6.        ]
 [  1.95617662]]
[[-21.28699644]
 [-22.56615757]
 [-11.54307334]
 [-11.00414974]
 [ -9.01026107]
 [ -2.6421288 ]
 [-25.77118075]
 [ -3.37445165]
 [-16.13437063]
 [ -5.51756487]
 [-10.87637038]
 [-28.92688734]
 [ -9.33874685]

0

In [152]:
n = len(X_train)
train_batches = [
                X_train[:,k:k+16]
                for k in range(0, n, 16)]
labels_batches = [
                one_hot(Y_train)[:,k:k+16]
                for k in range(0, n, 16)]

for batch, labels in zip(train_batches, labels_batches):
    z = batch
    u = labels


In [140]:
one_hot(Y_train).shape

(10, 41000)

In [154]:
z.shape

(784, 16)

In [158]:
for l in range(1, 3):
    print(l)

1
2
